In [26]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/ocrsampledataner/train50000ocred.csv
/kaggle/input/ocrsampledataner/train50000.csv


In [27]:
import pandas as pd
import os

In [28]:
datasetDir = '/kaggle/input/ocrsampledataner/'
df = pd.read_csv(os.path.join(datasetDir, 'train50000ocred.csv'))

In [29]:
df.reset_index(drop = True, inplace = True)
df = df.drop(columns = ['Unnamed: 0', 'image_link', 'imageName', 'ocrdata', 'result'])

In [30]:
df

group_id  entity_name     entity_value  \
0        997176      wattage     3.0 kilowatt   
1        403664        width   9.0 centimetre   
2        681445       height        11.8 inch   
3        599772       height       20.63 inch   
4        767202  item_weight       120.0 gram   
...         ...          ...              ...   
49995    145452       height   6.0 centimetre   
49996    664736        width         6.6 inch   
49997    952470        depth         8.5 inch   
49998    459516  item_weight  550.0 milligram   
49999    653767        depth  45.0 centimetre   

                                               cleandata  
0                                           ['3kW', '8']  
1                                       ['34 cm', '9cm']  
2                     ['19.5cm(7.6in)', '30cm (11.8in)']  
3      ['615mm/24.21in', '459mm/18.07in', '250mm/9.84...  
4      ['20Gm', '120Gms', '120Gm', '120Gm', '120Gm', ...  
...                                                  ...  
49995  ['2.36inch/6.0cm', '.77inch/4.5cm', '2.75inch/...  
49996                    ['15.7"', '2.2', '6.6"', 'CO2']  
49997           ['8.5"', '15"', '12.5"', '8.7"', '6.2"']  
49998  ['ServingSize:2 Capsules/Servings Per Containe...  
49999  ['45cm/18in', '45cm/18in', '45cm/18in', '45cm/...  

[50000 rows x 4 columns]

In [31]:
import re

# Abbreviation mapping
abbreviation_map = {
    'cm': 'centimetre',
    'mm': 'millimetre',
    'm': 'metre',
    'in': 'inch',
    'ft': 'foot',
    'yd': 'yard',
    'g': 'gram',
    'kg': 'kilogram',
    'mg': 'milligram',
    'µg': 'microgram',
    'lb': 'pound',
    'oz': 'ounce',
    't': 'ton',
    'ml': 'millilitre',
    'l': 'litre',
    'cl': 'centilitre',
    'dl': 'decilitre',
    'fl oz': 'fluid ounce',
    'gal': 'gallon',
    'pt': 'pint',
    'qt': 'quart',
    'cu ft': 'cubic foot',
    'cu in': 'cubic inch',
    'v': 'volt',
    'kv': 'kilovolt',
    'mv': 'millivolt',
    'w': 'watt',
    'kw': 'kilowatt'
}

# Unit and entity_name mapping (your map)
unit_map = {
    'width': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'depth': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'height': {'centimetre', 'foot', 'inch', 'metre', 'millimetre', 'yard'},
    'item_weight': {'gram', 'kilogram', 'microgram', 'milligram', 'ounce', 'pound', 'ton'},
    'maximum_weight_recommendation': {'gram', 'kilogram', 'microgram', 'milligram', 'ounce', 'pound', 'ton'},
    'voltage': {'kilovolt', 'millivolt', 'volt'},
    'wattage': {'kilowatt', 'watt'},
    'item_volume': {'centilitre', 'cubic foot', 'cubic inch', 'cup', 'decilitre', 'fluid ounce', 'gallon',
                    'imperial gallon', 'litre', 'microlitre', 'millilitre', 'pint', 'quart'}
}

# Function to preprocess a single string (helper)
def preprocess_string(text, entity_type):
    # Add a space between a number and an abbreviation (e.g., 65cm to 65 cm)
    text = re.sub(r'(\d+)([a-zA-Z]+)', r'\1 \2', text)

    # Replace abbreviations with full unit names
    for abbr, full in abbreviation_map.items():
        text = re.sub(fr'\b{abbr}\b', full, text)

    # Ensure units are fully written and check the map for each entity type
    if entity_type in unit_map:
        valid_units = unit_map[entity_type]
        for unit in valid_units:
            text = re.sub(fr'\b{unit.capitalize()}\b', unit, text.lower())  # Standardize capitalization

    return text

# Function to preprocess the 'cleandata' column
def preprocess_clean_data_row(clean_data_list, entity_type):
    # Process each string in the list individually
    if isinstance(clean_data_list, list):
        processed_list = [preprocess_string(item, entity_type) for item in clean_data_list]
        return processed_list
    else:
        # Handle cases where clean_data_list is not a list
        return [preprocess_string(clean_data_list, entity_type)]

# Applying the function to the DataFrame
def preprocess_clean_data_df(df):
    df['cleaned_data'] = df.apply(lambda row: preprocess_clean_data_row(row['cleandata'], row['entity_name']), axis=1)
    return df


In [32]:
# Assuming df is your DataFrame
df = preprocess_clean_data_df(df)

# Check the first few rows of the cleaned data
print(df[['cleandata', 'cleaned_data']].head())


                                           cleandata  \
0                                       ['3kW', '8']   
1                                   ['34 cm', '9cm']   
2                 ['19.5cm(7.6in)', '30cm (11.8in)']   
3  ['615mm/24.21in', '459mm/18.07in', '250mm/9.84...   
4  ['20Gm', '120Gms', '120Gm', '120Gm', '120Gm', ...   

                                        cleaned_data  
0                                    [['3 kw', '8']]  
1                [['34 centimetre', '9 centimetre']]  
2  [['19.5 centimetre(7.6 inch)', '30 centimetre ...  
3  [['615 millimetre/24.21 inch', '459 millimetre...  
4  [['20 gm', '120 gms', '120 gm', '120 gm', '120...  


In [33]:
df

group_id  entity_name     entity_value  \
0        997176      wattage     3.0 kilowatt   
1        403664        width   9.0 centimetre   
2        681445       height        11.8 inch   
3        599772       height       20.63 inch   
4        767202  item_weight       120.0 gram   
...         ...          ...              ...   
49995    145452       height   6.0 centimetre   
49996    664736        width         6.6 inch   
49997    952470        depth         8.5 inch   
49998    459516  item_weight  550.0 milligram   
49999    653767        depth  45.0 centimetre   

                                               cleandata  \
0                                           ['3kW', '8']   
1                                       ['34 cm', '9cm']   
2                     ['19.5cm(7.6in)', '30cm (11.8in)']   
3      ['615mm/24.21in', '459mm/18.07in', '250mm/9.84...   
4      ['20Gm', '120Gms', '120Gm', '120Gm', '120Gm', ...   
...                                                  ...   
49995  ['2.36inch/6.0cm', '.77inch/4.5cm', '2.75inch/...   
49996                    ['15.7"', '2.2', '6.6"', 'CO2']   
49997           ['8.5"', '15"', '12.5"', '8.7"', '6.2"']   
49998  ['ServingSize:2 Capsules/Servings Per Containe...   
49999  ['45cm/18in', '45cm/18in', '45cm/18in', '45cm/...   

                                            cleaned_data  
0                                        [['3 kw', '8']]  
1                    [['34 centimetre', '9 centimetre']]  
2      [['19.5 centimetre(7.6 inch)', '30 centimetre ...  
3      [['615 millimetre/24.21 inch', '459 millimetre...  
4      [['20 gm', '120 gms', '120 gm', '120 gm', '120...  
...                                                  ...  
49995  [['2.36 inch/6.0 centimetre', '.77 inch/4.5 ce...  
49996                  [['15.7"', '2.2', '6.6"', 'co2']]  
49997         [['8.5"', '15"', '12.5"', '8.7"', '6.2"']]  
49998  [['servingsize:2 capsules/servings per contain...  
49999  [['45 centimetre/18 inch', '45 centimetre/18 i...  

[50000 rows x 5 columns]

# Model Work

In [34]:
from transformers import BertTokenizerFast, AutoModelForTokenClassification
from sklearn.model_selection import train_test_split
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, SequentialSampler
import torch

In [35]:
def addContext(row):
    return f"For Group {row['group_id']}, the {row['entity_name']} is {row['entity_value']} from {row['cleaned_data']}."

def addSpecialContext(row):
    group_id_token = f'[GROUP_ID_{row["group_id"]}]'
    entity_name_token = f'[{row["entity_name"].upper()}]'

    return f"{group_id_token} {entity_name_token} is {row['entity_value']} from {row['cleaned_data']}."

#Preprocessing
df['context'] = df.apply(addContext, axis = 1)
df['specialContext'] = df.apply(addSpecialContext, axis = 1)

uniqueGroups = df['group_id'].unique()
uniqueEntities = df['entity_name'].unique()

specialGroups = [f'[group_id_{group_id}]' for group_id in uniqueGroups]
specialEntities = [f'[{entity_name}]' for entity_name in uniqueEntities]
specialTokens = specialGroups + specialEntities
specials = {'group_id': specialGroups, 'entity_name': specialEntities}

#trainText, valText, trainLabels, valLabels = train_test_split(df['specialContext'], df['entity_value'], random_state = 42, test_size = 0.2)

In [36]:
tokenizer = BertTokenizerFast.from_pretrained('bert-base-uncased')
tokenizer.add_tokens(specialTokens)

tokenizer.save_pretrained('/kaggle/working/nertokenizer')

# tokenizedInputs = tokenizer(df['specialContext'].tolist(), padding=True, truncation=True, return_tensors='pt')

/opt/conda/lib/python3.10/site-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


('/kaggle/working/nertokenizer/tokenizer_config.json',
 '/kaggle/working/nertokenizer/special_tokens_map.json',
 '/kaggle/working/nertokenizer/vocab.txt',
 '/kaggle/working/nertokenizer/added_tokens.json',
 '/kaggle/working/nertokenizer/tokenizer.json')

In [37]:
def label_tokens(contextual_data, entity_value, special_tokens):
    tokens = tokenizer.tokenize(contextual_data)
    entity_tokens = tokenizer.tokenize(entity_value)
    labels = ['O'] * len(tokens)

    for idx, token in enumerate(tokens):
        if token in special_tokens['group_id']:
            labels[idx] = 'B-GROUP_ID'
        elif token in special_tokens['entity_name']:
            labels[idx] = 'B-ENTITY_TYPE'

    for i in range(len(tokens) - len(entity_tokens) + 1):
        if tokens[i:i + len(entity_tokens)] == entity_tokens:
            labels[i] = 'B-ENTITY'
            for j in range(1, len(entity_tokens)):
                labels[i + j] = 'I-ENTITY'
            break
    
    return tokens, labels

In [ ]:
df['tokens'], df['labels'] = zip(*df.apply(lambda row: label_tokens(row['specialContext'], row['entity_value'], specials), axis = 1))
print(df[['specialContext', 'tokens', 'labels']].head())

Token indices sequence length is longer than the specified maximum sequence length for this model (886 > 512). Running this sequence through the model will result in indexing errors


In [ ]:
def map_labels_to_int(examples):
    label_list = {'B-ENTITY': 0, 'I-ENTITY': 1, 'O': 2, 'B-GROUP_ID': 3, 'B-ENTITY_TYPE': 4}
    examples['labels'] = [[label_list[label] for label in label_seq] for label_seq in examples['labels']]
    return examples

In [ ]:
label_mapping = {'B-ENTITY': 0, 'I-ENTITY': 1, 'O': 2, 'B-GROUP_ID': 3, 'B-ENTITY_TYPE': 4}

In [ ]:
def tokenize_and_align_labels(examples):
    tokenized_inputs = tokenizer(
        examples['tokens'],
        is_split_into_words=True,
        truncation=True,
        padding=True,
        max_length=512  # Adjust based on your data
    )
    
    labels = []
    for i, label in enumerate(examples['labels']):
        word_ids = tokenized_inputs.word_ids(batch_index=i)  # Map tokens to words
        previous_word_idx = None
        label_ids = []
        for word_idx in word_ids:
            if word_idx is None:
                label_ids.append(-100)  # Special tokens
            elif word_idx != previous_word_idx:
                label_ids.append(label[word_idx])  # Use the label of the word
            else:
                label_ids.append(-100)  # Subword tokens get -100 label
            previous_word_idx = word_idx
        labels.append(label_ids)

    tokenized_inputs['labels'] = labels
    return tokenized_inputs


# Converting DataFrame into Hugging Face Dataset

In [ ]:
from datasets import Dataset

dataset = Dataset.from_pandas(df[['specialContext', 'tokens', 'labels']])
dataset = dataset.map(map_labels_to_int, batched = True)

# dataset = dataset.rename_column('tokens', 'tokens')
# dataset = dataset.rename_column('labels', 'labels')

tokenized_dataset = dataset.map(tokenize_and_align_labels, batched = True)

print(tokenized_dataset[0])

In [ ]:
train_test_split = tokenized_dataset.train_test_split(test_size=0.2)
train_dataset = train_test_split['train']
test_dataset = train_test_split['test']

print(f"Training samples: {len(train_dataset)}")
print(f"Testing samples: {len(test_dataset)}")

In [ ]:
!pip install seqeval

In [ ]:
labelled = list(label_mapping.keys())

In [ ]:
from seqeval.metrics import classification_report, f1_score, accuracy_score, precision_score, recall_score
import numpy as np

# Define a function to align predictions with true labels
def align_predictions(predictions, label_ids):
    preds = np.argmax(predictions, axis=2)
    batch_size, seq_len = preds.shape
    
    # Convert predictions and labels to list format to align with token-level evaluation
    out_preds = [[] for _ in range(batch_size)]
    out_labels = [[] for _ in range(batch_size)]
    
    for i in range(batch_size):
        for j in range(seq_len):
            # Skip padding tokens (-100)
            if label_ids[i, j] != -100:
                out_preds[i].append(preds[i][j])
                out_labels[i].append(label_ids[i][j])
    
    return out_preds, out_labels

# Define the compute_metrics function
def compute_metrics(p):
    predictions, label_ids = p
    preds, labels = align_predictions(predictions, label_ids)

    # Convert to the string labels, if needed
    true_labels = [[labelled[l] for l in label] for label in labels]
    true_preds = [[labelled[p] for p in pred] for pred in preds]

    # Use seqeval to calculate precision, recall, and F1
    precision = precision_score(true_labels, true_preds)
    recall = recall_score(true_labels, true_preds)
    f1 = f1_score(true_labels, true_preds)
    accuracy = accuracy_score(true_labels, true_preds)

    return {
        "precision": precision,
        "recall": recall,
        "f1": f1,
        "accuracy": accuracy
    }

In [ ]:
from transformers import BertForTokenClassification

# Number of labels (B-ENTITY, I-ENTITY, O)
num_labels = len(label_mapping)

# Initialize the model
model = BertForTokenClassification.from_pretrained('bert-base-uncased', num_labels=num_labels)

# Resize token embeddings to accommodate new special tokens
model.resize_token_embeddings(len(tokenizer))

In [ ]:
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir='/kaggle/working/results/',          # Output directory
    num_train_epochs=3,              # Number of training epochs
    per_device_train_batch_size=32,  # Batch size for training
    per_device_eval_batch_size=32,   # Batch size for evaluation
    warmup_steps=500,                # Warmup steps
    weight_decay=0.01,               # Weight decay
    logging_dir='/kaggle/working/logs',            # Directory for storing logs
    logging_steps=10,                # Log every 10 steps
    evaluation_strategy="epoch",     # Evaluate at the end of each epoch
    save_total_limit=2,              # Only save 2 model checkpoints
    learning_rate=3e-5,              # Learning rate
    report_to="none",  # This disables W&B, TensorBoard, etc.
    run_name="local_run",  # Optional, if you want a specific run name
)


In [ ]:
from transformers import Trainer, DataCollatorForTokenClassification

# Define data collator
data_collator = DataCollatorForTokenClassification(tokenizer)

# Initialize the Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

In [ ]:
trainer.train()